In [1]:
# 读取配置
from lib import *
from lib.dataread import *
from lib.tools import *
from models.nerulforcastmodels import ex_Model,model_losss,brent_export_pdf,tansuanli_export_pdf,pp_export_pdf,model_losss_juxiting

import glob
import torch
torch.set_float32_matmul_precision("high")

sqlitedb = SQLiteHandler(db_name) 
sqlitedb.connect()

signature = BinanceAPI(APPID, SECRET)
etadata = EtaReader(signature=signature,
                        classifylisturl = classifylisturl,
                        classifyidlisturl=classifyidlisturl,
                        edbcodedataurl=edbcodedataurl,
                        edbcodelist=edbcodelist,
                        edbdatapushurl=edbdatapushurl,
                        edbdeleteurl=edbdeleteurl,
                        edbbusinessurl=edbbusinessurl
                        )
# 获取数据
if is_eta:
    # eta数据
    logger.info('从eta获取数据...')
    signature = BinanceAPI(APPID, SECRET)
    etadata = EtaReader(signature=signature,
                                classifylisturl = classifylisturl,
                                classifyidlisturl=classifyidlisturl,
                                edbcodedataurl=edbcodedataurl,
                                edbcodelist=edbcodelist,
                                edbdatapushurl=edbdatapushurl,
                                edbdeleteurl=edbdeleteurl,
                                edbbusinessurl=edbbusinessurl,
                                )
    df_zhibiaoshuju,df_zhibiaoliebiao =  etadata.get_eta_api_pp_data(data_set=data_set,dataset=dataset)  # 原始数据，未处理

    # 数据处理
    df = datachuli_juxiting(df_zhibiaoshuju,df_zhibiaoliebiao,y = y,dataset=dataset,add_kdj=add_kdj,is_timefurture=is_timefurture,end_time=end_time) 

else:
    logger.info('读取本地数据：'+os.path.join(dataset,data_set))
    df = getdata_juxiting(filename=os.path.join(dataset,data_set),y=y,dataset=dataset,add_kdj=add_kdj,is_timefurture=is_timefurture,end_time=end_time)  # 原始数据，未处理

# 更改预测列名称
df.rename(columns={y:'y'},inplace=True)
    
if is_edbnamelist:
    df = df[edbnamelist]     
df.to_csv(os.path.join(dataset,'指标数据.csv'), index=False)




读取本地数据：juxitingdataset\PP指标数据.xlsx
读取本地数据：juxitingdataset\PP指标数据.xlsx
getdata接收：juxitingdataset\PP指标数据.xlsx date 
getdata接收：juxitingdataset\PP指标数据.xlsx date 
删除两月不更新特征前数据量：(2515, 354)
删除两月不更新特征前数据量：(2515, 354)
删除两月不更新特征后数据量：(2515, 315)
删除两月不更新特征后数据量：(2515, 315)
删除预测列为空值的行后数据量：(771, 315)
删除预测列为空值的行后数据量：(771, 315)
删除全为空值的列后数据量：(771, 315)
删除全为空值的列后数据量：(771, 315)
d:\code\PriceForecast\lib\dataread.py:226: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  values.dropna(inplace=True,axis=0)
d:\code\PriceForecast\lib\dataread.py:226: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  values.dropna(inplace=True,axis=0)
d:\code\PriceFor

<Figure size 1000x1000 with 0 Axes>

In [3]:
# 保存最新日期的y值到数据库
# 取第一行数据存储到数据库中
first_row = df[['ds','y']].tail(1)
# 将最新真实值保存到数据库
if not sqlitedb.check_table_exists('trueandpredict'):
    first_row.to_sql('trueandpredict',sqlitedb.connection,index=False)
else:
    for row in first_row.itertuples(index=False):
        row_dict = row._asdict()
        row_dict['ds'] = row_dict['ds'].strftime('%Y-%m-%d %H:%M:%S')
        check_query = sqlitedb.select_data('trueandpredict',where_condition = f"ds = '{row.ds}'")
        if len(check_query) > 0:
            set_clause = ", ".join([f"{key} = '{value}'" for key, value in row_dict.items()])
            sqlitedb.update_data('trueandpredict',set_clause,where_condition = f"ds = '{row.ds}'")
            continue
        sqlitedb.insert_data('trueandpredict',tuple(row_dict.values()),columns=row_dict.keys())




更新数据sqlUPDATE trueandpredict SET ds = '2024-11-18 00:00:00', y = '7363.333333333333' WHERE ds = '2024-11-18 00:00:00'
更新数据sqlUPDATE trueandpredict SET ds = '2024-11-18 00:00:00', y = '7363.333333333333' WHERE ds = '2024-11-18 00:00:00'


In [11]:
import datetime
# 判断当前日期是不是周一
is_weekday = datetime.datetime.now().weekday() == 1
if is_weekday:
    logger.info('今天是周一，更新预测模型')
    # 计算最近20天预测残差最低的模型名称

    model_results = sqlitedb.select_data('trueandpredict',order_by = "ds DESC",limit = "20")
    # 删除空值率为40%以上的列
    print(model_results.shape)
    model_results = model_results.dropna(thresh=len(model_results)*0.6,axis=1)
    model_results = model_results.dropna()
    print(model_results.shape)
    modelnames  = model_results.columns.to_list()[2:] 
    for col in model_results[modelnames].select_dtypes(include=['object']).columns:
        model_results[col] = model_results[col].astype(np.float32)
    # 计算每个预测值与真实值之间的偏差率
    for model in modelnames:
        model_results[f'{model}_abs_error_rate'] = abs(model_results['y'] - model_results[model]) / model_results['y']

    # 获取每行对应的最小偏差率值
    min_abs_error_rate_values = model_results.apply(lambda row: row[[f'{model}_abs_error_rate' for model in modelnames]].min(), axis=1)
    # 获取每行对应的最小偏差率值对应的列名
    min_abs_error_rate_column_name = model_results.apply(lambda row: row[[f'{model}_abs_error_rate' for model in modelnames]].idxmin(), axis=1)
    print(min_abs_error_rate_column_name)
    # 将列名索引转换为列名
    min_abs_error_rate_column_name = min_abs_error_rate_column_name.map(lambda x: x.split('_')[0])
    # 取出现次数最多的模型名称
    most_common_model = min_abs_error_rate_column_name.value_counts().idxmax()
    logger.info(f"最近20天预测残差最低的模型名称：{most_common_model}")

    # 保存结果到数据库
    
    if not sqlitedb.check_table_exists('most_model'):
        sqlitedb.create_table('most_model',columns="ds datetime, most_common_model TEXT")
    sqlitedb.insert_data('most_model',(datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S'),most_common_model,),columns=('ds','most_common_model',))



今天是周一，更新预测模型
今天是周一，更新预测模型
最近20天预测残差最低的模型名称：NHITS
最近20天预测残差最低的模型名称：NHITS


(16, 23)
(12, 22)
1     TSMixerx_abs_error_rate
2          TCN_abs_error_rate
3        NHITS_abs_error_rate
4        NHITS_abs_error_rate
5     Informer_abs_error_rate
8        BiTCN_abs_error_rate
9     PatchTST_abs_error_rate
10     TSMixer_abs_error_rate
11       BiTCN_abs_error_rate
12     StemGNN_abs_error_rate
13    Informer_abs_error_rate
14     NLinear_abs_error_rate
dtype: object


In [13]:
if is_corr:
    df = corr_feature(df=df)

df1 = df.copy()  # 备份一下，后面特征筛选完之后加入ds y 列用
logger.info(f"开始训练模型...")
row,col = df.shape


开始训练模型...
开始训练模型...


In [ ]:
now = datetime.datetime.now().strftime('%Y%m%d%H%M%S')
# ex_Model(df,
#         horizon=horizon,
#         input_size=input_size,
#         train_steps=train_steps,
#         val_check_steps=val_check_steps,
#         early_stop_patience_steps=early_stop_patience_steps,
#         is_debug=is_debug,
#         dataset=dataset,
#         is_train=is_train,
#         is_fivemodels=is_fivemodels,
#         val_size=val_size,
#         test_size=test_size,
#         settings=settings,
#         now=now,
#         etadata = etadata,
#         modelsindex = modelsindex,
#         data = data,
#         is_eta=is_eta,
#         )


In [43]:
logger.info('模型训练完成')
# # 模型评估

pd.set_option('display.max_columns', 100)
# 计算预测评估指数
def model_losss_juxiting(sqlitedb):
    global dataset
    # 数据库查询最佳模型名称
    most_model = [sqlitedb.select_data('most_model',columns=['most_common_model'],order_by='ds desc',limit=1).values[0][0]]
    most_model_name = most_model[0]

    # 预测数据处理 predict
    df_combined = loadcsv(os.path.join(dataset,"cross_validation.csv"))  
    df_combined = dateConvert(df_combined)
    # 删除空列
    df_combined.dropna(axis=1,inplace=True)
     # 删除缺失值,预测过程不能有缺失值
    df_combined.dropna(inplace=True) 
    # 其他列转为数值类型
    df_combined = df_combined.astype({col: 'float32' for col in df_combined.columns if col not in ['cutoff','ds'] })
    # 使用 groupby 和 transform 结合 lambda 函数来获取每个分组中 cutoff 的最小值，并创建一个新的列来存储这个最大值
    df_combined['max_cutoff'] = df_combined.groupby('ds')['cutoff'].transform('max')

    # 然后筛选出那些 cutoff 等于 max_cutoff 的行，这样就得到了每个分组中 cutoff 最大的行，并保留了其他列
    df_combined = df_combined[df_combined['cutoff'] == df_combined['max_cutoff']]
    # 删除模型生成的cutoff列
    df_combined.drop(columns=['cutoff', 'max_cutoff'], inplace=True)
    # 获取模型名称
    modelnames  = df_combined.columns.to_list()[1:] 
    if 'y' in modelnames:
        modelnames.remove('y')
    df_combined3 = df_combined.copy()  # 备份df_combined,后面画图需要


    # 空的列表存储每个模型的MSE、RMSE、MAE、MAPE、SMAPE
    cellText = []

    # 遍历模型名称，计算模型评估指标  
    for model in modelnames:
        modelmse = mse(df_combined['y'], df_combined[model])
        modelrmse = rmse(df_combined['y'], df_combined[model])
        modelmae = mae(df_combined['y'], df_combined[model])
        # modelmape = mape(df_combined['y'], df_combined[model])
        # modelsmape = smape(df_combined['y'], df_combined[model])
        # modelr2 = r2_score(df_combined['y'], df_combined[model])
        cellText.append([model,round(modelmse, 3), round(modelrmse, 3), round(modelmae, 3)])
        
    model_results3 = pd.DataFrame(cellText,columns=['模型(Model)','平均平方误差(MSE)', '均方根误差(RMSE)',  '平均绝对误差(MAE)'])
    # 按MSE降序排列
    model_results3 = model_results3.sort_values(by='平均平方误差(MSE)', ascending=True)
    model_results3.to_csv(os.path.join(dataset,"model_evaluation.csv"),index=False)
    modelnames = model_results3['模型(Model)'].tolist()
    allmodelnames = modelnames.copy()
    # 保存5个最佳模型的名称
    if len(modelnames) > 5:
        modelnames = modelnames[0:5]
    with open(os.path.join(dataset,"best_modelnames.txt"), 'w') as f:
        f.write(','.join(modelnames) + '\n')


    # 根据最接近真实值的预测模型计算波动率，得到在波动率范围内的预测值确定通道边界

    best_models = pd.read_csv(os.path.join(dataset,'best_modelnames.txt'),header=None).values.flatten().tolist()
    def find_min_max_within_quantile(row):
        row = row[best_models]
        q10 = row.min()
        q90 = row.max()
        # 获取 row行最大最小值模型名称
        min_model = row[row == q10].idxmin()
        max_model = row[row == q90].idxmin()
        
        # # 判断flot值是否为空值
        # if pd.isna(q10) or pd.isna(q90):
        return pd.Series([q10, q90,min_model,max_model], index=['min_within_quantile','max_within_quantile','min_model','max_model'])

    # 遍历行
    df_combined3[['min_within_quantile', 'max_within_quantile','min_model','max_model']] = df_combined3.apply(find_min_max_within_quantile, axis=1)
    df_combined = df_combined.round(4)
    # print(df_combined3)

    
    # 去除有空值的行
    df_combined3.dropna(inplace=True)
    # 保存到数据库
    # df_combined3.to_sql('testandpredict_groupby', sqlitedb.connection, if_exists='replace', index=False)
    df_combined3.to_csv(os.path.join(dataset,"testandpredict_groupby.csv"),index=False)


    
    # 预测值与真实值对比图
    plt.rcParams['font.sans-serif'] = ['SimHei']
    plt.figure(figsize=(15, 10))
    # 设置有5个子图的画布
    for n,model in enumerate(modelnames[:5]):
        plt.subplot(3, 2, n+1)
        plt.plot(df_combined3['ds'], df_combined3['y'], label='真实值')
        plt.plot(df_combined3['ds'], df_combined3[model], label=model)
        plt.legend()
        plt.xlabel('日期')
        plt.ylabel('价格')
        plt.title(model+'拟合')
    plt.subplots_adjust(hspace=0.5)
    plt.savefig(os.path.join(dataset,'预测值与真实值对比图.png'), bbox_inches='tight')
    plt.close()
    
    # 历史数据+预测数据
    # 拼接未来时间预测
    df_predict  = loadcsv(os.path.join(dataset,'predict.csv'))
    df_predict.drop('unique_id',inplace=True,axis=1)
    df_predict.dropna(axis=1,inplace=True)

    try:
        df_predict['ds'] = pd.to_datetime(df_predict['ds'],format=r'%Y-%m-%d')
    except ValueError :
        df_predict['ds'] = pd.to_datetime(df_predict['ds'],format=r'%Y/%m/%d')

    # 取第一行数据存储到数据库中
    first_row = df_predict.head(1)
    first_row['ds'] = first_row['ds'].dt.strftime('%Y-%m-%d 00:00:00')
    # 将预测结果保存到数据库
    # if not sqlitedb.check_table_exists('trueandpredict'):
    #     first_row.to_sql('trueandpredict',sqlitedb.connection,index=False)
    # else:
    #     for col in first_row.columns:
    #             sqlitedb.add_column_if_not_exists('trueandpredict',col,'TEXT')
    #     for row in first_row.itertuples(index=False):
    #         row_dict = row._asdict()
    #         columns=row_dict.keys()
    #         check_query = sqlitedb.select_data('trueandpredict',where_condition = f"ds = '{row.ds}'")
    #         if len(check_query) > 0:
    #             set_clause = ", ".join([f"{key} = '{value}'" for key, value in row_dict.items()])
    #             sqlitedb.update_data('trueandpredict',set_clause,where_condition = f"ds = '{row.ds}'")
    #             continue
    #         sqlitedb.insert_data('trueandpredict',tuple(row_dict.values()),columns=columns)

    # 计算df_combined3[min_within_quantile]  和 df_combined3[most_model] 的方差
    diff = df_combined3['min_within_quantile']-df_combined3[most_model_name]
    var = diff.var()
    print('方差为：',var)
    df_predict['min_model'] = f'{most_model_name}_var_down'
    df_predict['max_model'] = f'{most_model_name}_var_up'
    # 找到大于最佳模型预测值-2倍方差的值
    df_predict['min_within_quantile'] = df_predict[most_model_name]-var
    df_combined3['min_within_quantile'] = df_combined3[most_model_name]-var
    # 找到小于最佳模型预测值+2倍方差的值
    df_predict['max_within_quantile'] = df_predict[most_model_name]+2*var
    df_combined3['max_within_quantile'] = df_combined3[most_model_name]+var
    print('最佳模型两倍方差')
    print(df_predict)
    df_predict2 = df_predict.copy()
    df_predict2['ds'] = df_predict2['ds'].dt.strftime('%Y-%m-%d 00:00:00')


    # # 将预测结果保存到数据库
    # # 判断表存在
    # if not sqlitedb.check_table_exists('testandpredict_groupby'):
    #     df_predict2.to_sql('testandpredict_groupby',sqlitedb.connection,index=False)
    # else:
    #     for row in df_predict2.itertuples(index=False):
    #         row_dict = row._asdict()
    #         check_query = sqlitedb.select_data('testandpredict_groupby',where_condition = f"ds = '{row.ds}'")
    #         if len(check_query) > 0:
    #             set_clause = ", ".join([f"{key} = '{value}'" for key, value in row_dict.items()])
    #             sqlitedb.update_data('testandpredict_groupby',set_clause,where_condition = f"ds = '{row.ds}'")
    #             continue
    #         sqlitedb.insert_data('testandpredict_groupby',tuple(row_dict.values()),columns=row_dict.keys())

    # # 计算每个预测值与真实值之间的偏差率
    # for model in allmodelnames:
    #     df_combined3[f'{model}_abs_error_rate'] = abs(df_combined3['y'] - df_combined3[model]) / df_combined3['y']

    # # 获取每行对应的最小偏差率值
    # min_abs_error_rate_values = df_combined3.apply(lambda row: row[[f'{model}_abs_error_rate' for model in allmodelnames]].min(), axis=1)
    # # 获取每行对应的最小偏差率值对应的列名
    # min_abs_error_rate_column_name = df_combined3.apply(lambda row: row[[f'{model}_abs_error_rate' for model in allmodelnames]].idxmin(), axis=1)
    # # 将列名索引转换为列名
    # min_abs_error_rate_column_name = min_abs_error_rate_column_name.map(lambda x: x.split('_')[0])
    # # 获取最小偏差率对应的模型的预测值
    # min_abs_error_rate_predictions = df_combined3.apply(lambda row: row[min_abs_error_rate_column_name[row.name]], axis=1)
    # # 将最小偏差率对应的模型的预测值添加到DataFrame中
    # df_combined3['min_abs_error_rate_prediction'] = min_abs_error_rate_predictions
    # df_combined3['min_abs_error_rate_column_name'] = min_abs_error_rate_column_name
    # df_combined3 = pd.concat([df_combined3, df_predict]).reset_index(drop=True)
    # # 判断 df 的数值列转为float
    # for col in df_combined3.columns:
    #     try:
    #         if col != 'ds':
    #             df_combined3[col] = df_combined3[col].astype(float)
    #             df_combined3[col] = df_combined3[col].round(2)
    #     except ValueError:
    #         pass
    # df_combined3.to_csv(os.path.join(dataset,"df_combined3.csv"),index=False) 
    
    #  # 历史价格+预测价格
    # df_combined3 = df_combined3[-50:] # 取50个数据点画图
    # # 历史价格
    # plt.figure(figsize=(20, 10))
    # plt.plot(df_combined3['ds'], df_combined3['y'], label='真实值')
    # # 颜色填充
    # plt.fill_between(df_combined3['ds'], df_combined3['min_within_quantile'], df_combined3['max_within_quantile'], alpha=0.2)
    # # plt.plot(df_combined3['ds'], df_combined3['min_abs_error_rate_prediction'], label='最小绝对误差', linestyle='--', color='orange')
    # # 网格
    # plt.grid(True)
    # # 显示历史值
    # for i, j in zip(df_combined3['ds'], df_combined3['y']):
    #     plt.text(i, j, str(j), ha='center', va='bottom')

    

    # for model in most_model:
    #     plt.plot(df_combined3['ds'], df_combined3[model], label=model,marker='o')
    # # 当前日期画竖虚线
    # plt.axvline(x=df_combined3['ds'].iloc[-horizon], color='r', linestyle='--')
    # plt.legend()
    # plt.xlabel('日期')
    # plt.ylabel('价格')
    
    # plt.savefig(os.path.join(dataset,'历史价格-预测值.png'), bbox_inches='tight')
    # plt.close()
       
    # # 预测值表格
    # fig, ax = plt.subplots(figsize=(20, 6))
    # ax.axis('off')  # 关闭坐标轴
    # # 数值保留2位小数
    # df_combined3 = df_combined3.round(2)
    # df_combined3 = df_combined3[-horizon:]
    # df_combined3['Day'] = [f'Day_{i}' for i in range(1,horizon+1)]
    # # Day列放到最前面
    # df_combined3 = df_combined3[['Day'] + list(df_combined3.columns[:-1])]
    # table = ax.table(cellText=df_combined3.values, colLabels=df_combined3.columns, loc='center')
    # #加宽表格
    # table.auto_set_font_size(False)
    # table.set_fontsize(10)

    # # 设置表格样式，列数据最小的用绿色标识
    # plt.savefig(os.path.join(dataset,'预测值表格.png'), bbox_inches='tight')
    # plt.close()
    # # plt.show()
       
    # # 可视化评估结果
    # plt.rcParams['font.sans-serif'] = ['SimHei']
    # fig, ax = plt.subplots(figsize=(20, 10))
    # ax.axis('off')  # 关闭坐标轴
    # table = ax.table(cellText=model_results3.values, colLabels=model_results3.columns, loc='center')
    # # 加宽表格
    # table.auto_set_font_size(False)
    # table.set_fontsize(10)

    # # 设置表格样式，列数据最小的用绿色标识
    # plt.savefig(os.path.join(dataset,'模型评估.png'), bbox_inches='tight')
    # plt.close()
    # return model_results3




logger.info('训练数据绘图ing')
model_results3 = model_losss_juxiting(sqlitedb)

logger.info('训练数据绘图end')



模型训练完成
模型训练完成
训练数据绘图ing
训练数据绘图ing
C:\Users\EDY\AppData\Local\Temp\ipykernel_8336\3546220967.py:119: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  first_row['ds'] = first_row['ds'].dt.strftime('%Y-%m-%d 00:00:00')
训练数据绘图end
训练数据绘图end


方差为： 783.5712373318445
最佳模型两倍方差
          ds      NHITS   Informer       LSTM  iTransformer    TSMixer  \
0 2024-11-19  7359.2050  7325.4340  7374.6274     7342.0290  7352.7837   
1 2024-11-20  7339.6730  7303.2560  7375.4020     7320.6665  7341.1157   
2 2024-11-21  7313.6357  7310.4240  7380.7524     7315.6226  7321.9478   
3 2024-11-22  7296.4775  7321.0250  7392.4790     7309.1006  7300.3430   
4 2024-11-25  7286.6978  7319.3916  7421.4077     7314.2144  7278.5120   

   TSMixerx   PatchTST        RNN        GRU        TCN      BiTCN  \
0  7343.613  7342.7300  7372.2515  7381.7810  7449.0703  7317.2397   
1  7339.045  7337.2275  7369.6200  7401.5024  7449.8086  7307.5415   
2  7387.099  7330.4020  7346.7344  7399.8660  7443.9330  7302.4478   
3  7376.246  7299.7417  7331.8857  7405.1810  7451.1577  7291.0230   
4  7335.186  7267.7980  7370.6760  7405.2725  7454.4453  7288.7314   

   DilatedRNN        MLP    DLinear    NLinear        TFT    StemGNN  \
0   7350.6070  7326.6610  7375

In [17]:
# 模型报告

logger.info('制作报告ing')
title = f'{settings}--{now}-预测报告' # 报告标题

pp_export_pdf(dataset=dataset,num_models = 5 if is_fivemodels else 22,time=end_time,
        reportname=reportname,sqlitedb=sqlitedb),

logger.info('制作报告end')
logger.info('模型训练完成')

制作报告ing
制作报告ing
开始绘制价差类指标的相关性直方图
开始绘制价差类指标的相关性直方图
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):


价差下正相关的特征值有： ['PP期货-丙烯价差（山东）/400DMA', 'PP-SC价差（7吨桶比）', '布伦特-PP价差（盘面）', '薄壁-拉丝价差（华北）', 'PP-FEI M4(含税成本)', '油制PP利润（华东）', 'PP-FEI M3(含税成本)', '价差：聚乙烯与乙烯（西北欧）', 'PP-FEI M2（含税成本）', 'PP-FEI M1（含税成本）', 'PP加权利润', '滨化PDH利润（1.169/含税）', 'PDH利润（山东/丙烯）', 'PP-FEI价差', '外采丙烯制聚丙烯利润（华东）', '5-9月差（PP）', '9-1月差（PP）']
正在绘制第1个特征PP期货-丙烯价差（山东）/400DMA与价格散点图...
正在绘制第2个特征PP-SC价差（7吨桶比）与价格散点图...


d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating

正在绘制第3个特征布伦特-PP价差（盘面）与价格散点图...
正在绘制第4个特征薄壁-拉丝价差（华北）与价格散点图...


d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating

...

d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating

正在绘制第5个特征BOPP 订单-成品天数与价格散点图...
需求下负相关的特征值有： ['PP下游成品库存天数', '中国CPP订单天数']
正在绘制第1个特征PP下游成品库存天数与价格散点图...


d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating

正在绘制第2个特征中国CPP订单天数与价格散点图...


绘制相关性总和的气泡图结束
绘制相关性总和的气泡图结束
制作报告end
制作报告end
模型训练完成
模型训练完成


In [ ]:
# 发送邮件
m = SendMail(
    username=username,
    passwd=passwd,
    recv=recv,
    title=title,
    content=content,
    file=max(glob.glob(os.path.join(dataset,'*.pdf')), key=os.path.getctime),
    ssl=ssl,
)
# m.send_mail()   
